In [1]:
import pandas as pd
import numpy as np

from datetime import date
from datetime import timedelta

In [2]:
# We load our data
df = pd.read_csv('static/customer_segmentation.csv', encoding='latin1')
df.head()

InvoiceNo StockCode                          Description  Quantity   
0    536365    85123A   WHITE HANGING HEART T-LIGHT HOLDER         6  \
1    536365     71053                  WHITE METAL LANTERN         6   
2    536365    84406B       CREAM CUPID HEARTS COAT HANGER         8   
3    536365    84029G  KNITTED UNION FLAG HOT WATER BOTTLE         6   
4    536365    84029E       RED WOOLLY HOTTIE WHITE HEART.         6   

      InvoiceDate  UnitPrice  CustomerID         Country  
0  12/1/2010 8:26       2.55     17850.0  United Kingdom  
1  12/1/2010 8:26       3.39     17850.0  United Kingdom  
2  12/1/2010 8:26       2.75     17850.0  United Kingdom  
3  12/1/2010 8:26       3.39     17850.0  United Kingdom  
4  12/1/2010 8:26       3.39     17850.0  United Kingdom

In [3]:
# We change our dates feature into a datetime type
df['InvoiceDate'] = pd.to_datetime(df['InvoiceDate'])

In [4]:
df['TotalAmount'] = df['Quantity'] * df['UnitPrice']
data_null = df[df['TotalAmount'] < 0]
data_null['Quantity'] = - data_null['Quantity']
data_null['TotalAmount'] = - data_null['TotalAmount']
data_null = data_null[['CustomerID', 'Description', 'Quantity', 'UnitPrice', 'TotalAmount']]

data_not_null = df[df['TotalAmount'] >= 0]
data_not_null['Quantity'] = - data_not_null['Quantity']
data_not_null['TotalAmount'] = - data_not_null['TotalAmount']
data_not_null = data_not_null[['CustomerID', 'Description', 'Quantity', 'UnitPrice', 'TotalAmount']]

df_concat = pd.concat([data_null, data_not_null])
df_concat = df_concat.drop_duplicates()
df_concat = df_concat.drop('TotalAmount', axis=1)

data_concat = pd.concat([df_concat, df])
null_quantity = data_concat[data_concat['Quantity'] < 0]
data_concat = data_concat.drop(null_quantity.index)
data_concat = data_concat.drop_duplicates(subset=['CustomerID', 'Description', 'Quantity', 'UnitPrice', 'TotalAmount'])
data_concat.head()

/var/folders/sm/_8w8tt415w56rr72t8421wj00000gn/T/ipykernel_4478/4209121508.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_null['Quantity'] = - data_null['Quantity']
/var/folders/sm/_8w8tt415w56rr72t8421wj00000gn/T/ipykernel_4478/4209121508.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  data_null['TotalAmount'] = - data_null['TotalAmount']
/var/folders/sm/_8w8tt415w56rr72t8421wj00000gn/T/ipykernel_4478/4209121508.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice f

CustomerID                         Description  Quantity  UnitPrice   
47     17850.0           HAND WARMER RED POLKA DOT         6       1.85  \
48     17850.0              HAND WARMER UNION JACK         6       1.85   
49     17850.0  WHITE HANGING HEART T-LIGHT HOLDER         6       2.55   
50     17850.0                 WHITE METAL LANTERN         6       3.39   
51     17850.0      CREAM CUPID HEARTS COAT HANGER         8       2.75   

   InvoiceNo StockCode         InvoiceDate         Country  TotalAmount  
47    536372     22632 2010-12-01 09:01:00  United Kingdom        11.10  
48    536372     22633 2010-12-01 09:01:00  United Kingdom        11.10  
49    536373    85123A 2010-12-01 09:02:00  United Kingdom        15.30  
50    536373     71053 2010-12-01 09:02:00  United Kingdom        20.34  
51    536373    84406B 2010-12-01 09:02:00  United Kingdom        22.00

In [5]:
def data_subset(data, beginning='2010-12-01', end='2011-12-09'):
    
    beginning = pd.to_datetime(beginning)
    end = pd.to_datetime(end)
    
    # Subsetting
    data = data[(data['InvoiceDate'] >= beginning) & (data['InvoiceDate'] <= end)]

    return data

In [6]:
def recency(data):
    new_data = data.copy()
    last_day = new_data['InvoiceDate'].max()

    recency = []
    for value in new_data['InvoiceDate']:
        result = last_day - value
        recency.append(result.days)
    
    new_data['Recency'] = recency

    return new_data

In [7]:
def frequency(data):
    new_data = data.copy()

    frequencies_series = new_data.groupby('CustomerID')['InvoiceNo'].unique()

    nb_orders = []
    for value in frequencies_series.values:
        nb_orders.append(len(value))

    indexes = frequencies_series.index

    df_freq = pd.DataFrame(nb_orders, columns=['NbOrder'])
    df_freq['CustomerID'] = indexes

    df_merge = new_data.merge(df_freq, on='CustomerID')

    df_merge['Frequency'] = df_merge['NbOrder']

    return df_merge

In [8]:
def monetary(data):
    new_data = data.copy()
    new_data['Monetary'] = new_data['Quantity'] * new_data['UnitPrice']

    return new_data

In [9]:
def rfm(data):
    new_data = data.copy()

    new_data = recency(new_data)
    new_data = frequency(new_data)
    new_data = monetary(new_data)

    df_rfm = new_data[['CustomerID', 'Recency', 'Frequency', 'Monetary']]

    monetary_sum = df_rfm.groupby('CustomerID')['Monetary'].sum()
    monetary_sum = pd.DataFrame(monetary_sum)
    monetary_sum = monetary_sum.reset_index()
    monetary_sum = monetary_sum[monetary_sum['Monetary'] > 5]

    df_rfm = df_rfm.drop('Monetary', axis=1)
    df_rfm = df_rfm.merge(monetary_sum, on='CustomerID')
    df_rfm = df_rfm.sort_values(['CustomerID', 'Recency'])
    df_rfm = df_rfm.drop_duplicates(subset='CustomerID')
    df_rfm = df_rfm.reset_index()
    df_rfm = df_rfm.drop(['index'], axis=1)

    return df_rfm

In [10]:
# We apply our functions to get the new features we are interested in
df_info = recency(data_concat)
df_info = frequency(df_info)
df_info = monetary(df_info)
df_info.head()

CustomerID                         Description  Quantity  UnitPrice   
0     17850.0           HAND WARMER RED POLKA DOT         6       1.85  \
1     17850.0              HAND WARMER UNION JACK         6       1.85   
2     17850.0  WHITE HANGING HEART T-LIGHT HOLDER         6       2.55   
3     17850.0                 WHITE METAL LANTERN         6       3.39   
4     17850.0      CREAM CUPID HEARTS COAT HANGER         8       2.75   

  InvoiceNo StockCode         InvoiceDate         Country  TotalAmount   
0    536372     22632 2010-12-01 09:01:00  United Kingdom        11.10  \
1    536372     22633 2010-12-01 09:01:00  United Kingdom        11.10   
2    536373    85123A 2010-12-01 09:02:00  United Kingdom        15.30   
3    536373     71053 2010-12-01 09:02:00  United Kingdom        20.34   
4    536373    84406B 2010-12-01 09:02:00  United Kingdom        22.00   

   Recency  NbOrder  Frequency  Monetary  
0      373        9          9     11.10  
1      373        9          9     11.10  
2      373        9          9     15.30  
3      373        9          9     20.34  
4      373        9          9     22.00

In [11]:
# We drop features we won't use
df_info = df_info.drop(['StockCode', 'Country', 'UnitPrice'], axis=1)
df_info.head()

CustomerID                         Description  Quantity InvoiceNo   
0     17850.0           HAND WARMER RED POLKA DOT         6    536372  \
1     17850.0              HAND WARMER UNION JACK         6    536372   
2     17850.0  WHITE HANGING HEART T-LIGHT HOLDER         6    536373   
3     17850.0                 WHITE METAL LANTERN         6    536373   
4     17850.0      CREAM CUPID HEARTS COAT HANGER         8    536373   

          InvoiceDate  TotalAmount  Recency  NbOrder  Frequency  Monetary  
0 2010-12-01 09:01:00        11.10      373        9          9     11.10  
1 2010-12-01 09:01:00        11.10      373        9          9     11.10  
2 2010-12-01 09:02:00        15.30      373        9          9     15.30  
3 2010-12-01 09:02:00        20.34      373        9          9     20.34  
4 2010-12-01 09:02:00        22.00      373        9          9     22.00

We apply our rfm function to have the list of CustomerID values that have a "Monetary" feature which is positive.

In [12]:
df_customers = rfm(df)
customers = df_customers['CustomerID'].unique()
customers

array([12347., 12348., 12349., ..., 18282., 18283., 18287.])

In [13]:
# We apply to get only the interesting IDs
df_info = df_info[df_info['CustomerID'].isin(customers)]
df_info.head()

CustomerID                         Description  Quantity InvoiceNo   
0     17850.0           HAND WARMER RED POLKA DOT         6    536372  \
1     17850.0              HAND WARMER UNION JACK         6    536372   
2     17850.0  WHITE HANGING HEART T-LIGHT HOLDER         6    536373   
3     17850.0                 WHITE METAL LANTERN         6    536373   
4     17850.0      CREAM CUPID HEARTS COAT HANGER         8    536373   

          InvoiceDate  TotalAmount  Recency  NbOrder  Frequency  Monetary  
0 2010-12-01 09:01:00        11.10      373        9          9     11.10  
1 2010-12-01 09:01:00        11.10      373        9          9     11.10  
2 2010-12-01 09:02:00        15.30      373        9          9     15.30  
3 2010-12-01 09:02:00        20.34      373        9          9     20.34  
4 2010-12-01 09:02:00        22.00      373        9          9     22.00

In [14]:
# We save as a CSV file
df_info.to_csv('static/customer_info.csv')